## Импорт библиотек


In [1]:
import requests      # Библиотека для отправки запросов
import numpy as np   # Библиотека для матриц, векторов и линала
import pandas as pd  # Библиотека для табличек 
import time          # Библиотека для времени
import re, os
import json
import datetime
from bs4 import BeautifulSoup 
from tqdm import tqdm
import pandas as pd

In [2]:
!pip install datetime

/home/baki/anaconda3/lib/python3.7/site-packages/secretstorage/dhcrypto.py:16: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/home/baki/anaconda3/lib/python3.7/site-packages/secretstorage/util.py:25: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes


In [3]:
page_link = 'http://lenta.ru/'

In [4]:
response = requests.get(page_link)
response

<Response [200]>

*200 ответ — соединение установлено и данные получены, всё чудесно!*

In [5]:
html = response.content

In [6]:
html[:1000]

b'<!DOCTYPE html><html><head><title>Lenta.ru - \xd0\x9d\xd0\xbe\xd0\xb2\xd0\xbe\xd1\x81\xd1\x82\xd0\xb8 \xd0\xa0\xd0\xbe\xd1\x81\xd1\x81\xd0\xb8\xd0\xb8 \xd0\xb8 \xd0\xbc\xd0\xb8\xd1\x80\xd0\xb0 \xd1\x81\xd0\xb5\xd0\xb3\xd0\xbe\xd0\xb4\xd0\xbd\xd1\x8f</title><meta content="Lenta.ru - \xd0\x9d\xd0\xbe\xd0\xb2\xd0\xbe\xd1\x81\xd1\x82\xd0\xb8 \xd0\xa0\xd0\xbe\xd1\x81\xd1\x81\xd0\xb8\xd0\xb8 \xd0\xb8 \xd0\xbc\xd0\xb8\xd1\x80\xd0\xb0 \xd1\x81\xd0\xb5\xd0\xb3\xd0\xbe\xd0\xb4\xd0\xbd\xd1\x8f" name="title" /><meta content="text/html; charset=utf-8" http-equiv="Content-Type" />\n<script type="text/javascript">window.NREUM||(NREUM={});NREUM.info={"beacon":"bam-cell.nr-data.net","errorBeacon":"bam-cell.nr-data.net","licenseKey":"66a8d51230","applicationID":"1241738","transactionName":"J19cQUoOWA0ERBoJUA1eHVxWBVEZ","queueTime":0,"applicationTime":356,"agent":""}</script>\n<script type="text/javascript">(window.NREUM||(NREUM={})).init={ajax:{deny_list:["bam-cell.nr-data.net"]}};(window.NREUM||(NREU

In [7]:
html[-1000:]

b'0x1")](x,o)}catch(b){a=[6,b],r=0}finally{n=i=0}if(5&a[0])throw a[1];return{value:a[0]?a[1]:void 0,done:!0}}([a,u]):(J=Object[b("0x1bc")]||function(x){for(var t,n=1,r=arguments[b("0x4b")];n<r;n++)for(var e in t=arguments[n])Object[b("0x11")][b("0x12")][b("0x1")](t,e)&&(x[e]=t[e]);return x})[b("0x10")](this,arguments)}}};(function(x,t,n,r){new(n=n||Promise)(function(e,i){function o(x){try{a(r[b("0x1be")](x))}catch(x){if(b("0x651")===b("0x652"))return s+h+f+x+s+"/"+h+f;i(x)}}function c(x){try{a(r[b("0x1bf")](x))}catch(b){i(b)}}function a(x){var t;x[b("0x51")]?e(x[b("0x52")]):((t=x[b("0x52")])instanceof n?t:new n(function(b){b(t)}))[b("0x8b")](o,c)}a((r=r[b("0x10")](x,t||[]))[b("0x1be")]())})})(void 0,void 0,void 0,function(){var x;return N(this,function(t){switch(t[b("0x1c3")]){case 0:return t[b("0x1c6")][b("0x59")]([0,2,,3]),[4,(new R)[b("0xf")]()];case 1:return t[b("0x1ca")](),[3,3];case 2:return x=t[b("0x1ca")](),Object(a.n)(x),[3,3];case 3:return[2]}})})}]);}();</script></body></htm

In [8]:
len(html)

418607

In [9]:
type(html)

bytes

In [10]:
!pip install fake_useragent

/home/baki/anaconda3/lib/python3.7/site-packages/secretstorage/dhcrypto.py:16: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/home/baki/anaconda3/lib/python3.7/site-packages/secretstorage/util.py:25: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes


In [11]:
from fake_useragent import UserAgent

In [12]:
UserAgent().Firefox

'Mozilla/5.0 (Windows NT 6.1; Win64; x64; rv:25.0) Gecko/20100101 Firefox/29.0'

In [13]:
class Collector():
    def __init__(self, *args, **kwargs):
        super(Collector, self).__init__(*args, **kwargs)
        self.startlink = 'https://lenta.ru/'
        self.user_agent = 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:21.0) Gecko/20130331 Firefox/21.0'
        self.headers = { 'User-Agent' : self.user_agent }
             
 
    def __call__(self,  states=None, **kwargs):
        response = []
        links = self.get_pages()

        for l in links[:300]:
            try:
                response.append(self.get_texts(l) )
                res = {
                    "res_utterances": [[response]],
                    "states": states,
                    "date": str(datetime.datetime.now())
                }
            except:
                print('Wrong link',l)
        return res
    
    
    def use_requests(self, link):
        return requests.get(link,headers=self.headers)
    
    def get_pages(self, link=''):
        lst = []
        cur_year = datetime.datetime.today().year
        for year in range(2010,cur_year):
            for month in range (1,2):
                if month <10:
                    month = "0" + str(month)
                for day in range(1,2):
                    if day<10:
                        day = "0" + str(day)
                    newlink = "https://lenta.ru/news/" + str(year) +"/"+str(month)+"/"+str(day)+"/"
                    r = self.use_requests(newlink)
                    refs=re.split('href="', re.split('<svg class="control_mini-icon control_mini-icon-prev">', re.split('">Все материалы</a></div></div></div><div id="context_3"></div></div></section><div id="root_footer">', r.text)[0])[1])    
                    for i in refs:
                        if i.startswith("/news/") or i.startswith("/article/"):
                            lst.append(re.split('">',i)[0])
        return list(set(lst))

    def get_texts(self, link):
       
        r = self.use_requests(self.startlink+link)
        text = re.split('</p></div></div><section class="b-', re.split('itemprop="articleBody"><p>',r.text)[1])[0]
        title, date, rubrics = self.get_metadata(r.text)
        return {'text':self.clean(text), 'link':link, 'title':title, 'date':date, 'rubrics':rubrics}
    
    def get_metadata(self, r_text):# Функция сбора метаданных.
        # дата
        date=re.split("  ", re.split("</time>", re.split('pubdate=""> ', r_text)[1])[0])[1]
        # рубрика новости
        rubrics=re.split(": ",re.split('<title>', r_text)[1])[1]
        # заголовок статьи
        title=re.split(":",re.split('<title>', r_text)[1])[0]
        
        return title, date, rubrics
        
    @staticmethod    
    def clean(text):
        
        text = BeautifulSoup(text, "lxml") #красивый суп
        text = text.get_text() 
        text = re.split('\n\n', text)[0]
        text = re.sub('\xa0', ' ', text)
        text = re.sub('&nbsp;', ' ', text)
        text = re.sub('&mdash;', ' -- ', text)
        text = re.sub('&shy;', '', text)
        text = re.sub('&laquo;', '"', text)
        text = re.sub('&raquo;', '"', text)
        text = re.sub('\xa0', ' ', text)
        text = re.sub('\u2009', ' ', text)
        return text

In [14]:
cr = Collector()
result = cr()

Wrong link /news/2018/01/01/page/2/
Wrong link /news/2011/01/01/page/2/
Wrong link /news/2017/01/01/russvk/
Wrong link /news/2021/11/23/router/
Wrong link /news/2015/01/02/
Wrong link /news/2021/11/23/sevpotok/
Wrong link /news/2021/11/22/kristigrud/
Wrong link /news/2021/11/23/todorenko_hate/
Wrong link /news/2020/12/30/novosib/
Wrong link /news/2021/11/23/rmblr/
Wrong link /news/2021/11/23/napadenie/
Wrong link /news/2021/11/23/tomashevski/
Wrong link /news/2021/11/23/proverka/
Wrong link /news/2020/12/30/attestats/
Wrong link /news/2021/11/23/rozenfake/
Wrong link /news/2021/11/23/revniviy/
Wrong link /news/2017/01/02/
Wrong link /news/2021/11/19/soviet_beer/
Wrong link /news/2021/11/19/message/
Wrong link /news/2018/01/02/
Wrong link /news/2021/11/23/kiany/
Wrong link /news/2016/01/01/page/2/
Wrong link /news/2019/01/01/page/2/
Wrong link /news/2021/11/23/foto/
Wrong link /news/2021/11/22/buzzz/
Wrong link /news/2020/12/30/dorogiprim/
Wrong link /news/2021/11/23/snizhenie/
Wrong li

In [16]:
result

{'res_utterances': [[[{'text': 'Сотрудники милиции вечером 31 декабря уничтожили в Хасавюрте четверых боевиков. Об этом сообщает РИА Новости со ссылкой на представителей МВД Дагестана. Один из ликвидированных членов незаконного бандформирования - глава боевиков по имени Умалат Магомедов, известный также под кличкой "Альбаро".Примерно в 22:00 милиционеры попытались остановить на Грозненской улице автомобиль "Жигули" для проверки. Находившиеся в машине люди начали стрелять в сотрудников правоохранительных органов и были уничтожены ответным огнем. О жертвах среди милиционеров не сообщается.На месте происшествия работают оперативники. Личности остальных боевиков устанавливаются.В начале декабря представители республиканского МВД заявили, что на территории Дагестана действуют шесть группировок боевиков: махачкалинская, хасавюртовско-кизилюртовская, губденская, гимринская, балаханинская и южнодагестанская. Численность каждой из них, по данным милиционеров, составляет от 10 до 40 человек.Пере

In [20]:
df = pd.DataFrame(result['res_utterances'][0][0])
df.shape

(246, 5)

In [21]:
df

text  \
0    Сотрудники милиции вечером 31 декабря уничтожи...   
1    Стоимость патента для мигранта в Москве с 1 ян...   
2    Президент Чечни Рамзан Кадыров принял участие ...   
3    Спящие более 11 или менее четырех часов в сутк...   
4    В Тульской области пьяный мужчина при задержан...   
..                                                 ...   
241  Целью совершенного в новогоднюю ночь в Стамбул...   
242  В Аксайком районе Ростовской области совершил ...   
243  В Яванском море 1 января возобновились поиски ...   
244  Участковый суд Вильнюса арестовал подозреваемо...   
245  Судебные приставы подарили Белгородскому зоопа...   

                                link  \
0          /news/2009/12/31/boeviks/   
1          /news/2015/01/01/migrant/   
2            /news/2010/01/01/voice/   
3            /news/2020/01/01/sleep/   
4             /news/2013/01/01/tula/   
..                               ...   
241        /news/2017/01/01/erdogan/   
242           /news/2016/01/01/heli/   
243  /news/2015/01/01/searchresumed/   
244         /news/2015/01/01/oficer/   
245           /news/2011/01/01/gift/   

                                                 title           date  \
0    В Дагестане уничтожили лидера боевиков &quot;А...  1 января 2010   
1    Патенты для работающих в Москве мигрантов подо...  1 января 2015   
2    Замаскированного под Деда Мороза Кадырова узна...  1 января 2010   
3                Объяснена опасность неправильного сна  1 января 2020   
4    Бросавшийся на автомобили туляк покусал полице...  1 января 2013   
..                                                 ...            ...   
241          Эрдоган назвал цель стамбульского теракта  1 января 2017   
242  Вертолет Bell совершил жесткую посадку в Росто...  1 января 2016   
243    Возобновились поиски пропавшего лайнера AirAsia  1 января 2015   
244  Суд арестовал подозреваемого в шпионаже литовс...  1 января 2015   
245  Приставы подарили Белгородскому зоопарку мрамо...  1 января 2011   

          rubrics  
0          Россия  
1          Москва  
2          Россия  
3           Наука  
4          Россия  
..            ...  
241      Политика  
242  Происшествия  
243      Общество  
244    Прибалтика  
245      Из жизни  

[246 rows x 5 columns]

### У выбранного сайта не смог обнаружить целевую переменную. Для второй части задания скачал предложенный датасет, с данными по отзывам на фильмы с сайта IMDB. Продолжение работы -> *DeBagg_Homework5.2*